Calculate the frequency of daisy drive alleles for different systems and release sizes.
<p>
Select values for the following:
* drive_init - the number of organisms to be released.
<p>
* C - either 'Single release' or 'Repeated releases every generation.' Repeated release option releases drive_init organisms.
<p>
* n - the number 
of elements in the daisy drive ranging from 1 element (A) to 6 elements (F->E->D->C->B->A)
<p>
* cost2 - the fitness cost of the payload in element A. Select none (0.02), moderate (0.1), or severe (0.4) 
<p>
* cost1 - the fitness cost of the other daisy drive elements. Select none (0), minor (0.05), or moderate (0.1)

In [25]:
num_elements = {'A':1, 'B->A':2, 'C->B->A':3, 'D->C->B->A':4, 'E->D->C->B->A':5, 'F->E->D->C->B->A':6}
#print num_elements.keys()

cost1_elements = {'none':0, 'minor':0.05, 'moderate':0.1}
#print cost1_elements.keys()

cost2_elements = {'none':0.02, 'moderate':0.01, 'severe':0.4}
#print cost2_elements.keys()

driveinit_elements = {
'One per thousand wild organisms': 0.001,
'One per hundred wild organisms': 0.01,
'One per ten wild organisms':0.1,
'One for every wild organism':1}
#print driveinit_elements.keys()

#repeated seeding frequency, or 0 if you don’t want repeated seeding
C_elements = {'Repeated seeding':1, 'No repeated seeding':0}

In [2]:
from IPython.display import display
from IPython.display import HTML
import IPython.core.display as di # Example: di.display_html('<h3>%s:</h3>' % str, raw=True)

# This line will hide code by default when the notebook is exported as HTML
di.display_html('<script>jQuery(function() {if (jQuery("body.notebook_app").length == 0) { jQuery(".input_area").toggle(); jQuery(".prompt").toggle();}});</script>', raw=True)

# This line will add a button to toggle visibility of code blocks, for use with the HTML export version
#di.display_html('''<button onclick="jQuery('.input_area').toggle(); jQuery('.prompt').toggle();">Toggle code</button>''', raw=True)

In [3]:
import percache
cache = percache.Cache("cache.txt")

import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

In [4]:
@cache
def daisy_drive(n, cost1, cost2, P, C, drive_init, t_max):
    # create file with the input parameters for the matlab function
    s = [n, cost1, cost2, P, C, drive_init, t_max]
    print s
    import csv
    with open('params.txt', 'w') as outfile:
        writer = csv.writer(outfile)
        writer.writerow(s)

    # execute matlab function (bash)
    !rm T.txt
    !rm Y.txt
    !/Applications/MATLAB_R2016a.app/bin/matlab -nodesktop -nosplash -r "cd('/Users/erika/daisy_drive');simulate_applet()"

    # read in matlab output files
    from numpy import genfromtxt
    T = genfromtxt('T.txt', delimiter=',')
    Y = genfromtxt('Y.txt', delimiter=',')
    return(T,Y)

In [5]:
def plot(n, cost1, cost2, C, drive_init):
    n = num_elements[n]
    cost1 = cost1_elements[cost1]
    cost2 = cost2_elements[cost2]
    drive_init = driveinit_elements[drive_init]
    
    fig, ax = plt.subplots(figsize=(4, 3),
                           subplot_kw={'axisbg':'#EEEEEE',
                                       'axisbelow':True})
    ax.grid(color='w', linewidth=2, linestyle='solid')
    
    if C == 'Repeated seeding':
        C = drive_init
    else:
        C = 0
        
    (T,Y) = daisy_drive(n, cost1, cost2, 1, C, drive_init, 200)

    for i in range(0, n):
        if n > 1:
            Y_i = [b[i] for b in Y]
        else:
            Y_i = Y
        ax.plot(T, Y_i,lw=5, alpha=0.4)
    #ax.set_xlim(0, 10)
    #ax.set_ylim(-1.1, 1.1)
    return fig

In [6]:
# hide silly little matplotlib warning
import warnings
warnings.filterwarnings('ignore')

In [26]:
from ipywidgets import StaticInteract, RangeWidget, RadioWidget

StaticInteract(plot,
               n=RadioWidget(['A', 'B->A', 'C->B->A', 'D->C->B->A', 'E->D->C->B->A', 'F->E->D->C->B->A']),
               cost1=RadioWidget(['none', 'minor', 'moderate']),
               cost2=RadioWidget(cost2_elements.keys()),
               C=RadioWidget(C_elements.keys()),
               drive_init=RadioWidget(driveinit_elements.keys()) )

In [12]:
cache.close()